In [ ]:
!unzip train_data.zip

Archive:  train_data.zip
   creating: train_data/
   creating: train_data/en/
   creating: train_data/en/replics/
  inflating: train_data/en/replics/train_rachel_replics.txt  
  inflating: train_data/en/replics/valid_rachel_replics.txt  
   creating: train_data/en/single/
  inflating: train_data/en/single/train_rachel_single.txt  
  inflating: train_data/en/single/valid_rachel_single.txt  


In [ ]:
!pip install peft datasets transformers[torch] accelerate -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.9/190.9 kB 1.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 4.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 280.0/280.0 kB 3.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 4.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 2.9 MB/s eta 0:00:00


In [ ]:
import os
import torch
import pathlib
import pandas as pd
from IPython.display import clear_output

In [ ]:
ROOT_DIR = os.path.abspath(os.getcwd())
ROOT_DIR

'/content'

По факту можно написать

In [ ]:
CHARACTER = "rachel"
model_type = "gpt2-medium"  # 'gpt2', 'gpt2-medium', 'gpt2-large'

In [ ]:
from transformers import AutoTokenizer
from transformers import pipeline
from transformers import TextDataset, DataCollatorForLanguageModeling
from transformers import Trainer, TrainingArguments,AutoModelWithLMHead

Training on monologues

In [ ]:
tokenizer = AutoTokenizer.from_pretrained(model_type)

tokenizer_config.json:   0%|          | 0.00/26.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/718 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

In [ ]:
block_size_ = 128

Define paths to training data

In [ ]:
path_to_single_data = './train_data/en/single/'
train_path = path_to_single_data + f'train_{CHARACTER}_single.txt'
test_path = path_to_single_data + f'valid_{CHARACTER}_single.txt'
train_path, test_path

('./train_data/en/single/train_rachel_single.txt',
 './train_data/en/single/valid_rachel_single.txt')

Create datasets

In [ ]:
def load_dataset(train_path,test_path,tokenizer):
    train_dataset = TextDataset(
          tokenizer=tokenizer,
          file_path=train_path,
          block_size=block_size_)

    test_dataset = TextDataset(
          tokenizer=tokenizer,
          file_path=test_path,
          block_size=block_size_)

    data_collator = DataCollatorForLanguageModeling(
        tokenizer=tokenizer, mlm=False,
    )
    return train_dataset,test_dataset,data_collator

train_dataset, test_dataset, data_collator = load_dataset(train_path, test_path, tokenizer)

/usr/local/lib/python3.10/dist-packages/transformers/data/datasets/language_modeling.py:53: FutureWarning: This dataset will be removed from the library soon, preprocessing should be handled with the 🤗 Datasets library. You can have a look at this example script for pointers: https://github.com/huggingface/transformers/blob/main/examples/pytorch/language-modeling/run_mlm.py
  warnings.warn(


In [ ]:
!mkdir ./models

In [ ]:
model = AutoModelWithLMHead.from_pretrained(model_type)
output_folder = f"./models/en_{model_type}_{CHARACTER}_mono"

/usr/local/lib/python3.10/dist-packages/transformers/models/auto/modeling_auto.py:1595: FutureWarning: The class `AutoModelWithLMHead` is deprecated and will be removed in a future version. Please use `AutoModelForCausalLM` for causal language models, `AutoModelForMaskedLM` for masked language models and `AutoModelForSeq2SeqLM` for encoder-decoder models.
  warnings.warn(


model.safetensors:   0%|          | 0.00/1.52G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

Define arguments for trainings

In [ ]:
training_args = TrainingArguments(
    output_dir = output_folder,
    overwrite_output_dir=True, #overwrite the content of the output directory
    num_train_epochs=3, # number of training epochs
    learning_rate=0.00001,  # learning rate
    per_device_train_batch_size=6, # batch size for training
    per_device_eval_batch_size=6,  # batch size for evaluation
    eval_steps = 200, # number of update steps between two evaluations
    save_steps = 200, # after # steps model is saved
    save_strategy = "steps",
    evaluation_strategy = "steps",
    dataloader_drop_last=True, # avoid an error with an incomplete batch
    fp16=False,
    save_total_limit = 3, # Only last 5 models are saved. Older ones are deleted.
    load_best_model_at_end=True,
    )

trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
)

In [ ]:
trainer.train()

There were missing keys in the checkpoint model loaded: ['lm_head.weight'].


TrainOutput(global_step=1056, training_loss=1.4579368432362874, metrics={'train_runtime': 877.3852, 'train_samples_per_second': 7.225, 'train_steps_per_second': 1.204, 'total_flos': 1471061900132352.0, 'train_loss': 1.4579368432362874, 'epoch': 3.0})

In [ ]:
trainer.save_model()

In [ ]:
# The name of the task to train.
TASK_NAME = f"{model_type}_mono_en_{CHARACTER}"

# The output directory where the fine-tuned model and checkpoints will be written.
OUTPUT_DIR = f'{ROOT_DIR}/outputs/{TASK_NAME}/'
pathlib.Path(OUTPUT_DIR).mkdir(parents=True, exist_ok=True)

CONFIG_NAME = "config.json"
WEIGHTS_NAME = f"{TASK_NAME}_pytorch_model.bin"

In [ ]:
def saver(model, OUTPUT_DIR, WEIGHTS_NAME):
    model_to_save = model.module if hasattr(model, 'module') else model  # Only save the model it-self

    # If we save using the predefined names, we can load using `from_pretrained`
    output_model_file = os.path.join(OUTPUT_DIR, WEIGHTS_NAME)
    output_config_file = os.path.join(OUTPUT_DIR, CONFIG_NAME)

    torch.save(model_to_save.state_dict(), output_model_file)
    model_to_save.config.to_json_file(output_config_file)

saver(model, OUTPUT_DIR, WEIGHTS_NAME)

In [ ]:
path_to_dialogs_data = './train_data/en/replics/'
train_path = path_to_dialogs_data + f'train_{CHARACTER}_replics.txt'
test_path = path_to_dialogs_data + f'valid_{CHARACTER}_replics.txt'
train_path, test_path

('./train_data/en/replics/train_rachel_replics.txt',
 './train_data/en/replics/valid_rachel_replics.txt')

In [ ]:
train_dataset, test_dataset, data_collator = load_dataset(train_path, test_path, tokenizer)

/usr/local/lib/python3.10/dist-packages/transformers/data/datasets/language_modeling.py:53: FutureWarning: This dataset will be removed from the library soon, preprocessing should be handled with the 🤗 Datasets library. You can have a look at this example script for pointers: https://github.com/huggingface/transformers/blob/main/examples/pytorch/language-modeling/run_mlm.py
  warnings.warn(


In [ ]:
model = AutoModelWithLMHead.from_pretrained(output_folder)
final_output_folder = f"./models/en_{model_type}_{CHARACTER}_replics"

/usr/local/lib/python3.10/dist-packages/transformers/models/auto/modeling_auto.py:1595: FutureWarning: The class `AutoModelWithLMHead` is deprecated and will be removed in a future version. Please use `AutoModelForCausalLM` for causal language models, `AutoModelForMaskedLM` for masked language models and `AutoModelForSeq2SeqLM` for encoder-decoder models.
  warnings.warn(


In [ ]:
training_args = TrainingArguments(
    output_dir = final_output_folder,
    overwrite_output_dir=True, #overwrite the content of the output directory
    num_train_epochs=5, # number of training epochs
    learning_rate=0.00001,  # learning rate
    lr_scheduler_type="linear",
    per_device_train_batch_size=6, # batch size for training
    per_device_eval_batch_size=6,  # batch size for evaluation
    eval_steps = 400, # number of update steps between two evaluations
    save_steps = 400, # after # steps model is saved
    save_strategy = "steps",
    evaluation_strategy = "steps",
    dataloader_drop_last=True, # avoid an error with an incomplete batch
    fp16=False,
    save_total_limit = 3, # Only last 5 models are saved. Older ones are deleted.
    load_best_model_at_end=True,
    )

trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
)

In [ ]:
trainer.train()

There were missing keys in the checkpoint model loaded: ['lm_head.weight'].


TrainOutput(global_step=1990, training_loss=1.986690410058103, metrics={'train_runtime': 1501.1605, 'train_samples_per_second': 7.957, 'train_steps_per_second': 1.326, 'total_flos': 2772171573166080.0, 'train_loss': 1.986690410058103, 'epoch': 5.0})

In [ ]:
trainer.save_model()

In [ ]:
# The name of the task to train.
TASK_NAME = f'{model_type}_mono_replics_en_{CHARACTER}'

# The output directory where the fine-tuned model and checkpoints will be written.
OUTPUT_DIR = f'{ROOT_DIR}/outputs/{TASK_NAME}/'
pathlib.Path(OUTPUT_DIR).mkdir(parents=True, exist_ok=True)

CONFIG_NAME = "config.json"
WEIGHTS_NAME = f"{TASK_NAME}_pytorch_model.bin"

saver(model, OUTPUT_DIR, WEIGHTS_NAME)

In [ ]:
chef = pipeline('text-generation', model="./models/en_gpt2-medium_rachel_replics", tokenizer=model_type)

In [ ]:
tmp = chef(f"<s>NOTFRIEND: Do you like Ross?\nRACHEL:")[0]['generated_text']
tmp = tmp[tmp.find(f"RACHEL: ") + len("RACHEL") + 2 : tmp.find('</s>')]
tmp

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


"I love him. I mean, for sure, but he's your only hope. Ross ruined everything."